In [8]:
import pandas as pd
import requests
import configparser
import sqlite3
import time

import numpy as np
import random

from sklearn.model_selection import train_test_split

import matplotlib.pyplot as plt
import japanize_matplotlib
import seaborn as sns
import pickle


from sklearn.preprocessing import OneHotEncoder
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

import joblib


In [212]:

def init_kr_db():
    # 'kr_data.db'データベース作成
    conn = sqlite3.connect('kr_data.db')
    c = conn.cursor()

    # summoners テーブルを作成
    c.execute('''
    CREATE TABLE IF NOT EXISTS summoners (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        account_id TEXT,
        rank TEXT
    )
    ''')
    c.execute('''
    CREATE TABLE IF NOT EXISTS matches (
        match_id TEXT PRIMARY KEY AUTOINCREMENT,
        champion_id INTEGER,
        role TEXT,
        lane TEXT,
        summoner_id INTEGER,
        gameId TEXT,
        FOREIGN KEY(summoner_id) REFERENCES summoners(id)
    )
    ''')
    conn.commit()
    conn.close()

if __name__ == "__main__":
    init_kr_db()

In [3]:
# config.iniファイルの読み込み　api_keyの取得
config_ini = configparser.ConfigParser()
config_ini.read('config.ini', encoding='utf-8')
api_key = config_ini['DEFAULT']['key']
# サーバー選択
REGION = 'kr'

NameError: name 'configparser' is not defined

In [339]:
# APIデバック
def validate_api_key(api_key, REGION):
    url = f'https://{REGION}.api.riotgames.com/lol/summoner/v4/summoners/by-name/サンプルサモナー名?api_key={api_key}'
    response = requests.get(url)
    if response.status_code == 200:
        print("APIキーは有効です")
    else:
        print(f"APIキーの確認エラー: {response.status_code} - {response.json()}")

validate_api_key(api_key, REGION)


APIキーの確認エラー: 403 - {'status': {'message': 'Forbidden', 'status_code': 403}}


In [8]:

# チャレンジャーのデータを取得
def get_challenger_summoners():
    url = f'https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/CHALLENGER/I?page=1&api_key=RGAPI-3ea7248e-4a6f-48d7-a303-f3ba423223d6'
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code}")
        return None
a = get_challenger_summoners()



NameError: name 'requests' is not defined

In [1]:
a

NameError: name 'a' is not defined

In [1]:
# チャレンジャーデータををsummoner_idsに保存
entries = a['entries']  # 'entries' キーのデータを取得
summoner_ids = [entry['summonerId'] for entry in entries]  # 'summonerId' をリストとして取得
print(summoner_ids)  # 'summonerId' のリストを表示    

NameError: name 'a' is not defined

In [253]:
CHALLENGER_leagueId = a['leagueId']

In [241]:
def get_account_ids(api_key, REGION):
    account_ids = []
    alldata= []
    puuid=[]
    url = f'https://{REGION}.api.riotgames.com/lol/summoner/v4/summoners/uCI6PYXCfnY5AXbARgWBxzSPBxso_-y80M4M0NYb3E__T8Y?api_key={api_key}'
    response = requests.get(url)
    if response.status_code == 200:
        data = response.json()
        account_ids.append(data['accountId'])
        puuid.append(data['puuid'])
        alldata.append(data)
        print(alldata)
    return account_ids

In [242]:
get_account_ids(api_key, REGION)

[{'id': 'uCI6PYXCfnY5AXbARgWBxzSPBxso_-y80M4M0NYb3E__T8Y', 'accountId': 'orQwfqLlFgQwsq1oBR9pyjsXjSQvZQxIJaVbE1Kk0dFwK_UWfl8TO6yE', 'puuid': 'n5QcnmmpMJRULHwzBrnPyiSoqCyzzET1wrk3V68rG3he5x0lbicEBnQQbhG3AOAhr67yRupAenUX9Q', 'profileIconId': 5980, 'revisionDate': 1718039938926, 'summonerLevel': 800}]


['orQwfqLlFgQwsq1oBR9pyjsXjSQvZQxIJaVbE1Kk0dFwK_UWfl8TO6yE']

In [256]:
def get_account_ids(api_key, REGION, summoner_ids):
    account_ids = []
    puuids = []
    all_data = []

    for i, summoner_id in enumerate(summoner_ids, start=1):
        url = f'https://{REGION}.api.riotgames.com/lol/summoner/v4/summoners/{summoner_id}?api_key={api_key}'
        response = requests.get(url)
        if response.status_code == 200:
            data = response.json()
            account_ids.append(data['accountId'])
            puuids.append(data['puuid'])
            all_data.append(data)
            print(f"Summoner ID: {summoner_id} -> Account ID: {data['accountId']}, PUUID: {data['puuid']}")
        else:
            print(f"Error: {response.status_code} for Summoner ID: {summoner_id}")
            print(response.json())

        # リクエストの制限を考慮して待機
        if i % 100 == 0:
            time.sleep(70)
        elif i % 20 == 0:
            time.sleep(10)

    return account_ids, puuids, all_data


In [262]:
account_ids, puuids, all_data = get_account_ids(api_key, REGION, summoner_ids)

print("Account IDs:", account_ids)
print("PUUIDs:", puuids)
print("All Data:", all_data)

Summoner ID: A1_ZbShZDBRR139bQeaVNcLH9YxeoF07MDnUuEW0kM_lpB4 -> Account ID: aTIcoeQR_OFtxwry17skZR4Xxx2CISFH1tsgVi0Me0rhVP4ikf11HQ97, PUUID: osVbkz4K1dXIj3DcQOH42RWgJ6kmC5AearRm7BUZzsPHPL5OgdXydo9avzmC5-eha8LbDj44sztm6Q
Summoner ID: W_ta5Bj_4va9G_Vxq4OzttzrZma18E1HvdcfQbGx04rEDCOg_rGjST958Q -> Account ID: s71y1LGQwSbXpV5g7XoVmGH7aY0Nr1egOLvN335NNljFwMJ7CsSPjfzB, PUUID: t6cbzT1151qpzEHRUQYxb6GXj8amTMQlM8RzVq5cBFsg9EHnbs0NjQP_sjm_IHYeZxwyO4ukaIFwWA
Summoner ID: dSIA9_W9D5Z-xAh5ihh3dzpOIzcEgnNqkb3qOXwjRQ7UzWwJLBbUfj70Fg -> Account ID: hsbH_2s6-346dmFeUq2yStmLq0cX29304Uda277QY4IBNfXOJ5N2V7bn, PUUID: U2UDvgKAZz31eUtMrBeeVuqN3yqNl7MjXz9n30kWoMQ71VCgCpd-ft0Ak89RYu7J3ClTz-OFNcS-Rw
Summoner ID: 4DbXQRkEzziy88nAU_dqUhLHuErI-d7MqYwsUSssJ0E4LYM -> Account ID: 85KY-vky3dLOcLY0QPw1vwQllLS9SZKwgfzma_ySMvvijqXXlK4Kmrj6, PUUID: JxMIZzkYaTQW_uu8cMJUrKT1He_o7FUxVGcSL_mBYYdRdGdxv_ldzZ0_wiQSFFzP8br-Sn5-Bp30Ow
Summoner ID: x5he2BjTRuTseg-BbG_YngTqdChlHVdgZSayuYOVoCGywRs -> Account ID: dIfAkxci5KFT5N6VFK_-iA

In [298]:
# わかりづらいけどaccountIdです
summoner_data

(['aTIcoeQR_OFtxwry17skZR4Xxx2CISFH1tsgVi0Me0rhVP4ikf11HQ97',
  's71y1LGQwSbXpV5g7XoVmGH7aY0Nr1egOLvN335NNljFwMJ7CsSPjfzB',
  'hsbH_2s6-346dmFeUq2yStmLq0cX29304Uda277QY4IBNfXOJ5N2V7bn',
  '85KY-vky3dLOcLY0QPw1vwQllLS9SZKwgfzma_ySMvvijqXXlK4Kmrj6',
  'dIfAkxci5KFT5N6VFK_-iALIP8bLzp_smF1tbfQuBtoOiPDeWMJNvnMv',
  'GaxclkhG0nL6Q99AT3NzdBpghbW0_RHSVm6OEjW9M7U0',
  'IF0PIqmhNItGeHaNJolo6D9JE2NmyRtgI1J1wRUzx36fspRMRvM0amGi',
  '3hpFIlNWvvEX78vEtVCE3E76s8C-tckW1OsZTtcqND-ogVbIMHrtYt7f',
  'eCQSNQ_7YkC8WaMDQg1L10XDXLjNRirE8HTbSoFKQGpdHKSDL9Ff3eb-',
  'UDpQzDrxymZ-kpT17PYwwD6P3SAWUTGUGlQVDxwV5YZTx5-LZiU1peLL',
  'ZGLt6lnmWPWa2DD8dYz_cB9Cub2_f1ZvSk-UtckgHLfvYoeL7nGIOkfZ',
  'bDUxW_ruwj0fhagNZ8Tl8Rxgu1A4Utaxlhu0jmA2MsRi',
  '3X9txeLiwPGOlSZCW5SSjQO3i6_qgS8n4PezC3_dd863hEg',
  'rgVQ_ygAEmi8Em3TaVvcWT087uWSf_1Ic3n4QBmRgnvOmYVQCM0iwm4u',
  'xuxF0AfZ8HW9dSJPneRxP-d14SQwIWhXYvsntP11Wefxwmo',
  '1gn6wC7xvkIm9Lx7gUjC6X0CFA3Ek0Q4hDDyvl9OIXalFD1wKwxJhq7R',
  'mTaqmfSk5-hvvZUfoLTqoUOeeGEDD06jMEua7XKUXin66yU

In [295]:
# チャレンジャーデータとpuuidをsqliteに
def info_account_id(account_ids, puuids):
    # データベースに接続
    conn = sqlite3.connect('kr_data.db')
    c = conn.cursor()
    # データの挿入
    for account_id, puuid_id in zip(account_ids, puuids):
        c.execute('''
        INSERT OR REPLACE INTO summoners(account_id, rank, puuid)
        VALUES(?,?,?)
        ''', (account_id, 'CHALLENGER', puuid_id))

    # 変更を保存して接続を閉じる
    conn.commit()
    conn.close()

In [296]:
info_account_id(account_ids, puuids)

In [297]:
# summonersを確認する
import sqlite3

dbname = 'kr_data.db'
conn = sqlite3.connect(dbname)
cur = conn.cursor()

# terminalで実行したSQL文と同じようにexecute()に書く
cur.execute('SELECT * FROM summoners')

# 中身を全て取得するfetchall()を使って、printする。
print(cur.fetchall())

cur.close()
conn.close()


[(601, 'aTIcoeQR_OFtxwry17skZR4Xxx2CISFH1tsgVi0Me0rhVP4ikf11HQ97', 'CHALLENGER', 'osVbkz4K1dXIj3DcQOH42RWgJ6kmC5AearRm7BUZzsPHPL5OgdXydo9avzmC5-eha8LbDj44sztm6Q'), (602, 's71y1LGQwSbXpV5g7XoVmGH7aY0Nr1egOLvN335NNljFwMJ7CsSPjfzB', 'CHALLENGER', 't6cbzT1151qpzEHRUQYxb6GXj8amTMQlM8RzVq5cBFsg9EHnbs0NjQP_sjm_IHYeZxwyO4ukaIFwWA'), (603, 'hsbH_2s6-346dmFeUq2yStmLq0cX29304Uda277QY4IBNfXOJ5N2V7bn', 'CHALLENGER', 'U2UDvgKAZz31eUtMrBeeVuqN3yqNl7MjXz9n30kWoMQ71VCgCpd-ft0Ak89RYu7J3ClTz-OFNcS-Rw'), (604, '85KY-vky3dLOcLY0QPw1vwQllLS9SZKwgfzma_ySMvvijqXXlK4Kmrj6', 'CHALLENGER', 'JxMIZzkYaTQW_uu8cMJUrKT1He_o7FUxVGcSL_mBYYdRdGdxv_ldzZ0_wiQSFFzP8br-Sn5-Bp30Ow'), (605, 'dIfAkxci5KFT5N6VFK_-iALIP8bLzp_smF1tbfQuBtoOiPDeWMJNvnMv', 'CHALLENGER', 'FnJWglsE3MfDHQ1kwJiYQnEPyBIOllH5ROCBw2vONgONX50BEInfPS2gg-j178cxg09iA39KLwqsyQ'), (606, 'GaxclkhG0nL6Q99AT3NzdBpghbW0_RHSVm6OEjW9M7U0', 'CHALLENGER', 'W8rLIOQ_9Da7eBss6kE16A_8kxQ_dNMNEa_3-eoTzf4L4MY5Wdug68QhItFeINXkYGRNewtn13FxFg'), (607, 'IF0PIqmhNItGeHaNJolo6D9JE2

In [274]:
conn = sqlite3.connect('kr_data.db')
# カーソルを作成
cursor = conn.cursor()
# テーブルの存在を確認するSQLクエリ
table_name = 'summoners'
check_table_query = f"SELECT name FROM sqlite_master WHERE type='table' AND name='{table_name}'"
# SQLクエリを実行
cursor.execute(check_table_query)
# 結果を取得
result = cursor.fetchone()
# テーブルの存在を確認
if result:
    print(f"{table_name} テーブルは存在します。")
else:
    print(f"{table_name} テーブルは存在しません。")
# 接続を閉じる
conn.close()

summoners テーブルは存在します。


In [291]:
# テーブルの列を確認

def get_table_columns(table_name):
    conn = sqlite3.connect('kr_data.db')
    c = conn.cursor()
    
    # PRAGMA table_infoを使用してテーブルの列情報を取得
    c.execute(f'PRAGMA table_info({table_name})')
    columns_info = c.fetchall()
    
    # 列名のリストを作成
    columns = [column[1] for column in columns_info]
    
    conn.close()
    return columns

def main():
    table_name = 'summoners'
    
    # テーブルの列名を取得
    columns = get_table_columns(table_name)
    print(f"Columns in table '{table_name}':")
    for column in columns:
        print(column)

if __name__ == "__main__":
    main()

Columns in table 'summoners':
id
account_id
rank
puuid


In [190]:
def fetch_column_data(db_name, table_name, column_name):
    conn = sqlite3.connect(db_name)
    c = conn.cursor()
    
    # 指定した列の情報を取得
    c.execute(f'SELECT {column_name} FROM {table_name}')
    rows = c.fetchall()
    
    conn.close()
    return rows

def main():
    db_name = 'kr_data.db'
    table_name = 'summoners'
    column_name = 'account_id'  # 取得したい列名を指定

    column_data = fetch_column_data(db_name, table_name, column_name)
    for row in column_data:
        print(row)

if __name__ == "__main__":
    main()


('8Je-G_XQkyw_LyOYPiTnjnQIHPHBxouXovYdscwA06jzSFcwUFaIHSIr',)
('pUMgsXZBqt0oqWpVofrG6N15lUEQXcOe583vME56GpzQojcDtTHmzFui',)
('1QhMX0RQaB2ihvHDs2mO2wobwE7osZlqSKgBX2QGeO6UJSeYaGwjcr8m',)
('SXI3Dr0cv3gkZXESOns67f6rkAL4IBgMwNQUpW8dzN_RCzHd03RqiwQM',)
('f2mcNZfP2ruTDvOtMgh6RJOlnoa0MxioIP67Vibdg-6hmriPw7qT0DgY',)
('O--VHbbkuF9oe3wKIqZ3ySfcm5KI7SX19UQKrevAgb5rorBiaY3lpXHv',)
('zNaYE7wR1ruefD7TEpGV6qmzWn8NKu9rux7VDI-McjhU0TfuzUMjpadF',)
('29-CX43NX8NZEll-Cenj8xm7WzqW2fDvQ-0wDnvBggkjgh4',)
('9WPKO5UyeFJyiFwbwN6WrDTwjjfXbm19ZgRaH5ELKEI813E',)
('h0W10be7_43ppoXEEUnpm-of2LzdgZBtIRv1Wx9i5wLR16g',)
('hsbH_2s6-346dmFeUq2yStmLq0cX29304Uda277QY4IBNfXOJ5N2V7bn',)
('tbw6SVTF1JwqY65ECGGNJ6HsKhGje6n8bFfkUVp1yPxJ1CM',)
('m9y0KHBJhc14GmYKzzG67IHuwhWDP6qsxh4pnllvAZcQ2UCTDMTle5Dz',)
('orQwfqLlFgQwsq1oBR9pyjsXjSQvZQxIJaVbE1Kk0dFwK_UWfl8TO6yE',)
('PuHLvKk8cKijllENq15Xhl82420Nwi2CxSIuc8hNdtqxH82zyZbp1Mge',)
('fvYhwP3czXeqkXlQHQf-0YJlkBeDSG4hbl_1kGhVWeme0je_8XJuDh2f',)
('vORnadS3sfZnMN4knqTchL9VhqpKMxlWMuIEtR6G5Y

In [2]:
def get_account_ids(api_key, REGION, summoner_data):
    account_ids = []
    for i, summoner_id in enumerate(summoner_ids, start=1):
        url = f'https://{REGION}.api.riotgames.com/lol/summoner/v4/summoners/{summoner_data}?api_key={api_key}'
        response = requests.get(url)
        if response.status_code == 200:
            matchlist_data = response.json()
            account_ids.append(matchlist_data)
            print(f"Summoner ID: {summoner_id} -> Account ID: {matchlist_data['accountId']}")
        else:
            print(f"Error: {response.status_code} for Summoner ID: {summoner_id}")
            print(response.json())

        # リクエストの制限を考慮して待機
        if i % 100 == 0:
            time.sleep(70)
        elif i % 20 == 0:
            time.sleep(10)

    return account_ids
f = get_account_ids(api_key, REGION, summoner_data)

NameError: name 'api_key' is not defined

In [203]:
def get_matchlist_by_account(api_key, REGION):
    url = f'https://{REGION}.api.riotgames.com/lol/match/v4/matchlists/by-account/SXI3Dr0cv3gkZXESOns67f6rkAL4IBgMwNQUpW8dzN_RCzHd03RqiwQM?api_key={api_key}'
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()['matches']
    else:
        print(f"Error: {response.status_code}")
        return None

# 関数を呼び出して結果を取得

d = get_matchlist_by_account(api_key, REGION,)



Error: 403


In [204]:
d

In [316]:
puuids

['osVbkz4K1dXIj3DcQOH42RWgJ6kmC5AearRm7BUZzsPHPL5OgdXydo9avzmC5-eha8LbDj44sztm6Q',
 't6cbzT1151qpzEHRUQYxb6GXj8amTMQlM8RzVq5cBFsg9EHnbs0NjQP_sjm_IHYeZxwyO4ukaIFwWA',
 'U2UDvgKAZz31eUtMrBeeVuqN3yqNl7MjXz9n30kWoMQ71VCgCpd-ft0Ak89RYu7J3ClTz-OFNcS-Rw',
 'JxMIZzkYaTQW_uu8cMJUrKT1He_o7FUxVGcSL_mBYYdRdGdxv_ldzZ0_wiQSFFzP8br-Sn5-Bp30Ow',
 'FnJWglsE3MfDHQ1kwJiYQnEPyBIOllH5ROCBw2vONgONX50BEInfPS2gg-j178cxg09iA39KLwqsyQ',
 'W8rLIOQ_9Da7eBss6kE16A_8kxQ_dNMNEa_3-eoTzf4L4MY5Wdug68QhItFeINXkYGRNewtn13FxFg',
 'SQN6fTvwOiOvFT3WcpYwbeVciko_C4LS7Kr6AjEv8GjHtSoTjOZco3B-gSftRkxwOur6hvxmwYKUFg',
 'IlbX1RZIfXy7nIRgfgJ2RaFQNgFLgMAo17gEJ2DiXo80NBT0onk5O4McgsHYThVo-q3QJG8FCyeoMA',
 'v2Ojs9VoB_pCRBmmr5BZA_CWXE2ggFe8u5_L2t79KakCw6vmms-dJctW0omcOOYkAq0yEcy04auKVg',
 'wMRUK9XGgENIi2PgAFZPn3VOmq3JASBchCtsTGbnbhJ7oV1cqDouY4HM-bHo4HFBuybpH65e_y8qxg',
 '6EVAMnwDGF8aB18SEPf1ZOBz8j8wt_3uYwdBwPhvcwk-Kq7RY1fWvgbNKmt6eHVpRJ-jasFofX9gDQ',
 '_XEEqE74YZxITbgeI29e-8opnFklD5xvUW-xv0PuRpCVxCUL5I6hAzcPl3PydYghsHqH5lzR2StrtA',
 'K1

In [496]:
def matchlist_puu(api_key, region, puuids):
    all_matchlists = []
    x = 1
    for puuid in puuids:
        # url = f'https://{region}.api.riotgames.com/lol/match/v5/matches/by-puuid/{puuid}/ids?start=0&count=50&api_key={api_key}'
        url = f'https://asia.api.riotgames.com/lol/match/v5/matches/by-puuid/{puuid}/ids?start=0&count=100&api_key=RGAPI-9ad4c443-b5de-47e3-9a74-7b22a5f3bfed'
        response = requests.get(url)
        if response.status_code == 200:
            matchlist = response.json()
            all_matchlists.append(matchlist)
            print(f"PUUID: {puuid} -> Matchlist: {matchlist}")
        else:
            print(f"Error: {response.status_code} for PUUID: {puuid}")
            print(response.json())

        # リクエストの制限を考慮して待機
        if x % 100 == 0:
            time.sleep(70)
        elif x % 20 == 0:
            time.sleep(10)
        x = x + 1
    
    return all_matchlists

In [497]:
region = 'asia'
matchlists = matchlist_puu(api_key, region, puuids)
for matchlist in matchlists:
    print(matchlist)

PUUID: osVbkz4K1dXIj3DcQOH42RWgJ6kmC5AearRm7BUZzsPHPL5OgdXydo9avzmC5-eha8LbDj44sztm6Q -> Matchlist: ['KR_7115283387', 'KR_7114471346', 'KR_7113243497', 'KR_7112390592', 'KR_7112355495', 'KR_7111789330', 'KR_7111741440', 'KR_7111669522', 'KR_7111318612', 'KR_7111214326', 'KR_7111153581', 'KR_7111030891', 'KR_7108800100', 'KR_7108739257', 'KR_7108665217', 'KR_7108596000', 'KR_7108546457', 'KR_7108416494', 'KR_7108390199', 'KR_7108347579', 'KR_7108327019', 'KR_7108156092', 'KR_7107771768', 'KR_7107743982', 'KR_7107712243', 'KR_7107424226', 'KR_7107337600', 'KR_7107311416', 'KR_7107133585', 'KR_7107097054', 'KR_7107069254', 'KR_7107024714', 'KR_7107008748', 'KR_7106837946', 'KR_7106831230', 'KR_7106776187', 'KR_7106724460', 'KR_7106676976', 'KR_7106641508', 'KR_7106514068', 'KR_7105694569', 'KR_7105627284', 'KR_7104546557', 'KR_7104491982', 'KR_7104294832', 'KR_7104236488', 'KR_7104027743', 'KR_7103942992', 'KR_7103068431', 'KR_7102849424', 'KR_7102772647', 'KR_7102711228', 'KR_7102641049'

In [351]:
matchlists

[['KR_7107364029',
  'KR_7107302105',
  'KR_7107262350',
  'KR_7107234039',
  'KR_7106549720',
  'KR_7106476804',
  'KR_7106450061',
  'KR_7106405274',
  'KR_7106367267',
  'KR_7106321156',
  'KR_7106296028',
  'KR_7106264680',
  'KR_7106219943',
  'KR_7106200340',
  'KR_7105262687',
  'KR_7105228468',
  'KR_7105208062',
  'KR_7104603785',
  'KR_7104550452',
  'KR_7104519140',
  'KR_7104455030',
  'KR_7104368461',
  'KR_7104318051',
  'KR_7104248909',
  'KR_7104213802',
  'KR_7104153767',
  'KR_7104092460',
  'KR_7104054819',
  'KR_7104014193',
  'KR_7103480767',
  'KR_7103486022',
  'KR_7103472471',
  'KR_7103464600',
  'KR_7103453917',
  'KR_7103452361',
  'KR_7103446210',
  'KR_7103440080',
  'KR_7103281353',
  'KR_7103231135',
  'KR_7103111716',
  'KR_7103052271',
  'KR_7102964765',
  'KR_7102911203',
  'KR_7102825103',
  'KR_7102774110',
  'KR_7102313802',
  'KR_7102254856',
  'KR_7102213539',
  'KR_7102184567',
  'KR_7101863165',
  'KR_7101853405',
  'KR_7101835842',
  'KR_710182

In [466]:
def test_matchlist_puu(api_key, region, puuids):
    all_matchlists = []
    x = 1
    for puuid in puuids:
        # url = f'https://{region}.api.riotgames.com/lol/match/v5/matches/by-puuid/{puuid}/ids?start=0&count=50&api_key={api_key}'
        url = f'https://asia.api.riotgames.com/lol/match/v5/matches/by-puuid/{puuid}/ids?start=0&count=10&api_key=RGAPI-53ae178e-6496-4ac9-80a0-d62680f9eb8a'
        response = requests.get(url)
        if response.status_code == 200:
            test_matchlist = response.json()
            all_matchlists.append(matchlist)
            print(f"PUUID: {puuid} -> Matchlist: {matchlist}")
        else:
            print(f"Error: {response.status_code} for PUUID: {puuid}")
            print(response.json())

        # リクエストの制限を考慮して待機
        if x % 100 == 0:
            time.sleep(70)
        elif x % 20 == 0:
            time.sleep(10)
        x = x + 1
    
    return all_matchlists

In [467]:
region = 'asia'
matchlists = test_matchlist_puu(api_key, region, puuids)
for test_matchlist in matchlists:
    print(matchlist)

PUUID: osVbkz4K1dXIj3DcQOH42RWgJ6kmC5AearRm7BUZzsPHPL5OgdXydo9avzmC5-eha8LbDj44sztm6Q -> Matchlist: ['KR_7107364029', 'KR_7107302105', 'KR_7107262350', 'KR_7107234039', 'KR_7106549720', 'KR_7106476804', 'KR_7106450061', 'KR_7106405274', 'KR_7106367267', 'KR_7106321156', 'KR_7106296028', 'KR_7106264680', 'KR_7106219943', 'KR_7106200340', 'KR_7105262687', 'KR_7105228468', 'KR_7105208062', 'KR_7104603785', 'KR_7104550452', 'KR_7104519140', 'KR_7104455030', 'KR_7104368461', 'KR_7104318051', 'KR_7104248909', 'KR_7104213802', 'KR_7104153767', 'KR_7104092460', 'KR_7104054819', 'KR_7104014193', 'KR_7103480767', 'KR_7103486022', 'KR_7103472471', 'KR_7103464600', 'KR_7103453917', 'KR_7103452361', 'KR_7103446210', 'KR_7103440080', 'KR_7103281353', 'KR_7103231135', 'KR_7103111716', 'KR_7103052271', 'KR_7102964765', 'KR_7102911203', 'KR_7102825103', 'KR_7102774110', 'KR_7102313802', 'KR_7102254856', 'KR_7102213539', 'KR_7102184567', 'KR_7101863165', 'KR_7101853405', 'KR_7101835842', 'KR_7101823914'

In [366]:
def get_testmatch_data(region, test_matchlist):
    url = f'https://{region}.api.riotgames.com/lol/match/v5/matches/{test_matchlist}?api_key=RGAPI-b5745b4c-b3b6-406b-8598-1d80e7520a74'
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code} for Match ID: {test_matchlist}")
        return None

def extract_match_info(match_data):
    if match_data is None:
        return None

    participant_info_list = []

    for participant in match_data['info']['participants']:
        participant_info = {
            'match_id': match_data['metadata']['matchId'],
            'game_duration': match_data['info']['gameDuration'],
            'championId': participant['championId'],
            'kills': participant['kills'],
            'deaths': participant['deaths'],
            'assists': participant['assists'],
            'total_damage_dealt': participant['totalDamageDealt'],
            'gold_earned': participant['goldEarned'],
            'vision_score': participant['visionScore'],
            'win': participant['win'],
            'lane': participant['individualPosition'],
            'team_id': participant['teamId']
        }
        participant_info_list.append(participant_info)

    return participant_info_list

all_participant_info = []
x = 0
for match_id in test_matchlist:
    x = x + 1
    match_data = get_testmatch_data(region, match_id)
    if match_data:
        participant_info_list = extract_match_info(match_data)
        all_participant_info.extend(participant_info_list)
        if x % 70 == 0:
            time.sleep(70)
        elif x % 20 == 0:
            time.sleep(10)


# プレイヤーデータフレーム
df_participants = pd.DataFrame(all_participant_info)

# マッチIDごとにグループ化して表示
grouped = df_participants.groupby('match_id')

for match_id, group in grouped:
    print(f"Match ID: {match_id}")
    print(group)

Match ID: KR_7098152566
          match_id  game_duration  championId  kills  deaths  assists  \
990  KR_7098152566            914          24      1       3        2   
991  KR_7098152566            914          76     13       1        7   
992  KR_7098152566            914         166      8       1        6   
993  KR_7098152566            914         145      2       1       10   
994  KR_7098152566            914         111      5       1       15   
995  KR_7098152566            914          23      3       3        0   
996  KR_7098152566            914         876      2       6        1   
997  KR_7098152566            914          18      1       6        1   
998  KR_7098152566            914          22      0       7        3   
999  KR_7098152566            914          16      1       7        3   

     total_damage_dealt  gold_earned  vision_score    win     lane  team_id  
990               51780         4956             6   True      TOP      100  
991             

In [368]:
df_participants


match_id  game_duration  championId  kills  deaths  assists  \
0    KR_7107364029           1102          69      4       2        1   
1    KR_7107364029           1102         421      0       4        5   
2    KR_7107364029           1102         517      3       2        2   
3    KR_7107364029           1102          81      5       5        1   
4    KR_7107364029           1102          99      2       8        6   
..             ...            ...         ...    ...     ...      ...   
995  KR_7098152566            914          23      3       3        0   
996  KR_7098152566            914         876      2       6        1   
997  KR_7098152566            914          18      1       6        1   
998  KR_7098152566            914          22      0       7        3   
999  KR_7098152566            914          16      1       7        3   

     total_damage_dealt  gold_earned  vision_score    win     lane  team_id  
0                100977         7685            16  False      TOP      100  
1                120697         5937            12  False   JUNGLE      100  
2                 56999         6296            13  False   MIDDLE      100  
3                 67319         7172            15  False   BOTTOM      100  
4                 21423         5561            46  False  UTILITY      100  
..                  ...          ...           ...    ...      ...      ...  
995               83326         6976             7  False      TOP      200  
996              101210         5600            10  False   JUNGLE      200  
997               49233         4899            12  False   MIDDLE      200  
998               37482         4397            11  False   BOTTOM      200  
999                7809         3816            22  False  UTILITY      200  

[1000 rows x 12 columns]

In [377]:
df = df_participants

In [379]:
import pandas as pd
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

# データ読み込み


# 特徴量とターゲット変数の分離
X = df.drop(columns=['win', 'match_id'])  # win列とmatch_id列を除く
y = df['win']

# カテゴリ列と数値列の分離
categorical_features = ['championId', 'lane', 'team_id']
numeric_features = ['kills', 'deaths', 'assists', 'total_damage_dealt', 'gold_earned', 'vision_score', 'game_duration']

# 前処理の設定
preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), numeric_features),
        ('cat', OneHotEncoder(), categorical_features)
    ])

# データ前処理パイプライン
pipeline = Pipeline(steps=[('preprocessor', preprocessor)])

# データの前処理
X_processed = pipeline.fit_transform(X)

# matchIDでグループ化
grouped = df.groupby('match_id')

print(f'X_processed shape: {X_processed.shape}')

X_processed shape: (1000, 150)


In [380]:
import numpy as np

# パラメータ
alpha = 0.1  # 学習率
gamma = 0.6  # 割引率
epsilon = 0.1  # ε-greedyの探索率

# 状態数とアクション数を定義
state_size = X_processed.shape[1]
action_size = 2  # 例として勝敗（勝ち/負け）

# Qテーブルの初期化
q_table = np.zeros((state_size, action_size))

# Q-learningアルゴリズム
for episode in range(1000):  # エピソード数
    for match_id, group in grouped:
        # 各試合ごとのデータ前処理
        X_match = group.drop(columns=['win', 'match_id'])
        y_match = group['win']
        X_match_processed = pipeline.transform(X_match).astype(int)
        
        # 初期状態を設定
        state = 0  # サンプルコードのため、最初の状態を0と仮定
        done = False

        while not done:
            # ε-greedyポリシーに基づくアクション選択
            if np.random.uniform(0, 1) < epsilon:
                action = np.random.choice(action_size)  # ランダムなアクション
            else:
                action = np.argmax(q_table[state])  # Qテーブルに基づくアクション

            # 実際の報酬と次の状態を取得（ここでは仮定的に設定）
            next_state = state  # 状態遷移（サンプルコードのため固定）
            reward = 1 if (action == 1 and y_match.iloc[0]) else -1  # 報酬（仮定）

            done = True  # 1ステップで終了（例として）

            # Q値の更新
            old_value = q_table[state, action]
            next_max = np.max(q_table[next_state])
            q_table[state, action] = (1 - alpha) * old_value + alpha * (reward + gamma * next_max)

            state = next_state

print("Q-learning training completed.")


Q-learning training completed.


In [381]:
import numpy as np

# 学習済みのQテーブルを保存
np.save('q_table.npy', q_table)


In [389]:
# テスト用の試合取得
def get_sample_testmatch_data(region):
    url = f'https://{region}.api.riotgames.com/lol/match/v5/matches/KR_7098152566?api_key=RGAPI-53ae178e-6496-4ac9-80a0-d62680f9eb8a'
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code} for Match ID:")
        return None

def extract_match_info(match_data):
    if match_data is None:
        return None

    sample_participant_info_list = []

    for participant in match_data['info']['participants']:
        participant_info = {
            'game_duration': match_data['info']['gameDuration'],
            'championId': participant['championId'],
            'kills': participant['kills'],
            'deaths': participant['deaths'],
            'assists': participant['assists'],
            'total_damage_dealt': participant['totalDamageDealt'],
            'gold_earned': participant['goldEarned'],
            'vision_score': participant['visionScore'],
            'win': participant['win'],
            'lane': participant['individualPosition'],
            'team_id': participant['teamId']
        }
        sample_participant_info_list.append(participant_info)

    return participant_info_list




# プレイヤーデータフレーム
df_sample_participants = pd.DataFrame(all_participant_info)

# マッチIDごとにグループ化して表示
grouped = df_sample_participants.groupby('match_id')

for match_id, group in grouped:
    print(f"Match ID: {match_id}")
    print(group)

NameError: name 'KR_7098152566' is not defined

In [390]:
df_sample_participants

match_id  game_duration  championId  kills  deaths  assists  \
0    KR_7107364029           1102          69      4       2        1   
1    KR_7107364029           1102         421      0       4        5   
2    KR_7107364029           1102         517      3       2        2   
3    KR_7107364029           1102          81      5       5        1   
4    KR_7107364029           1102          99      2       8        6   
..             ...            ...         ...    ...     ...      ...   
995  KR_7098152566            914          23      3       3        0   
996  KR_7098152566            914         876      2       6        1   
997  KR_7098152566            914          18      1       6        1   
998  KR_7098152566            914          22      0       7        3   
999  KR_7098152566            914          16      1       7        3   

     total_damage_dealt  gold_earned  vision_score    win     lane  team_id  
0                100977         7685            16  False      TOP      100  
1                120697         5937            12  False   JUNGLE      100  
2                 56999         6296            13  False   MIDDLE      100  
3                 67319         7172            15  False   BOTTOM      100  
4                 21423         5561            46  False  UTILITY      100  
..                  ...          ...           ...    ...      ...      ...  
995               83326         6976             7  False      TOP      200  
996              101210         5600            10  False   JUNGLE      200  
997               49233         4899            12  False   MIDDLE      200  
998               37482         4397            11  False   BOTTOM      200  
999                7809         3816            22  False  UTILITY      200  

[1000 rows x 12 columns]

In [391]:
q_table = np.load('q_table.npy')

# 新しい試合データの読み込み（仮定）
new_match_data = df_sample_participants  # ここに新しい試合データのファイルパスを指定

# 新しい試合データの前処理
X_new_processed = (new_match_data, pipeline)

# 初期状態を設定（仮定: 最初の状態を0とする）
state = 0

# Qテーブルに基づくアクション選択
action = np.argmax(q_table[state])  # Qテーブルに基づくアクション

# 予測結果の表示
result = 'Win' if action == 1 else 'Lose'
print(f'The predicted result for the match is: {result}')

The predicted result for the match is: Win


In [468]:
# test用
# マッチの詳細なデータ取得並びにデータフレーム化

def get_match_data(region, match_id):
    url = f'https://{region}.api.riotgames.com/lol/match/v5/matches/{match_id}?api_key=RGAPI-53ae178e-6496-4ac9-80a0-d62680f9eb8a'
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code} for Match ID: {match_id}")
        return None

def extract_match_info(match_data, match_id):
    if match_data is None:
        return None

    participant_info_list = []

    for participant in match_data['info']['participants']:
        participant_info = {
            'match_id': match_id,
            'game_duration': match_data['info']['gameDuration'],
            'champion_id': participant['championId'],
            'kills': participant['kills'],
            'deaths': participant['deaths'],
            'assists': participant['assists'],
            'total_damage_dealt': participant['totalDamageDealt'],
            'gold_earned': participant['goldEarned'],
            'vision_score': participant['visionScore'],
            'win': 1 if participant['win'] else 0,
            'team_id': participant['teamId']
        }
        participant_info_list.append(participant_info)

    return participant_info_list



all_participant_info = []
x = 0

for match_id in test_matchlist:
    match_data = get_match_data(region, match_id)
    x = x + 1
    if match_data:
        participant_info_list = extract_match_info(match_data, match_id)
        all_participant_info.extend(participant_info_list)
        if x % 70 == 0:
            time.sleep(70)
        elif x % 20 == 0:
            time.sleep(10)

# プレイヤーデータフレーム
df_participants = pd.DataFrame(all_participant_info)

# 結果の表示
print(df_participants.head())


        match_id  game_duration  champion_id  kills  deaths  assists  \
0  KR_7107364029           1102           69      4       2        1   
1  KR_7107364029           1102          421      0       4        5   
2  KR_7107364029           1102          517      3       2        2   
3  KR_7107364029           1102           81      5       5        1   
4  KR_7107364029           1102           99      2       8        6   

   total_damage_dealt  gold_earned  vision_score  win  team_id  
0              100977         7685            16    0      100  
1              120697         5937            12    0      100  
2               56999         6296            13    0      100  
3               67319         7172            15    0      100  
4               21423         5561            46    0      100  


In [469]:
df_participants

match_id  game_duration  champion_id  kills  deaths  assists  \
0    KR_7107364029           1102           69      4       2        1   
1    KR_7107364029           1102          421      0       4        5   
2    KR_7107364029           1102          517      3       2        2   
3    KR_7107364029           1102           81      5       5        1   
4    KR_7107364029           1102           99      2       8        6   
..             ...            ...          ...    ...     ...      ...   
995  KR_7098152566            914           23      3       3        0   
996  KR_7098152566            914          876      2       6        1   
997  KR_7098152566            914           18      1       6        1   
998  KR_7098152566            914           22      0       7        3   
999  KR_7098152566            914           16      1       7        3   

     total_damage_dealt  gold_earned  vision_score  win  team_id  
0                100977         7685            16    0      100  
1                120697         5937            12    0      100  
2                 56999         6296            13    0      100  
3                 67319         7172            15    0      100  
4                 21423         5561            46    0      100  
..                  ...          ...           ...  ...      ...  
995               83326         6976             7    0      200  
996              101210         5600            10    0      200  
997               49233         4899            12    0      200  
998               37482         4397            11    0      200  
999                7809         3816            22    0      200  

[1000 rows x 11 columns]

In [499]:
matchlists

[['KR_7115283387',
  'KR_7114471346',
  'KR_7113243497',
  'KR_7112390592',
  'KR_7112355495',
  'KR_7111789330',
  'KR_7111741440',
  'KR_7111669522',
  'KR_7111318612',
  'KR_7111214326',
  'KR_7111153581',
  'KR_7111030891',
  'KR_7108800100',
  'KR_7108739257',
  'KR_7108665217',
  'KR_7108596000',
  'KR_7108546457',
  'KR_7108416494',
  'KR_7108390199',
  'KR_7108347579',
  'KR_7108327019',
  'KR_7108156092',
  'KR_7107771768',
  'KR_7107743982',
  'KR_7107712243',
  'KR_7107424226',
  'KR_7107337600',
  'KR_7107311416',
  'KR_7107133585',
  'KR_7107097054',
  'KR_7107069254',
  'KR_7107024714',
  'KR_7107008748',
  'KR_7106837946',
  'KR_7106831230',
  'KR_7106776187',
  'KR_7106724460',
  'KR_7106676976',
  'KR_7106641508',
  'KR_7106514068',
  'KR_7105694569',
  'KR_7105627284',
  'KR_7104546557',
  'KR_7104491982',
  'KR_7104294832',
  'KR_7104236488',
  'KR_7104027743',
  'KR_7103942992',
  'KR_7103068431',
  'KR_7102849424',
  'KR_7102772647',
  'KR_7102711228',
  'KR_710264

In [515]:
# マッチの詳細なデータ取得並びにデータフレーム化


def get_match_data(region, match_id):
    url = f'https://{region}.api.riotgames.com/lol/match/v5/matches/{match_id}?api_key=RGAPI-b9685aa5-4e26-4851-9eea-d8ab50d0c738'
    response = requests.get(url)
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code} for Match ID: {match_id}")
        return None

def extract_match_info(match_data, match_id):
    if match_data is None:
        return None

    participant_info_list = []

    for participant in match_data['info']['participants']:
        participant_info = {
            'match_id': match_id,
            'game_duration': match_data['info']['gameDuration'],
            'champion_id': participant['championId'],
            'kills': participant['kills'],
            'deaths': participant['deaths'],
            'assists': participant['assists'],
            'total_damage_dealt': participant['totalDamageDealt'],
            'gold_earned': participant['goldEarned'],
            'vision_score': participant['visionScore'],
            'win': 1 if participant['win'] else 0,
            'team_id': participant['teamId']
        }
        participant_info_list.append(participant_info)

    return participant_info_list

all_participant_info = []
x = 0

for match_id in matchlists:
    for match2_id in match_id:
        match_data = get_match_data(region, match2_id)
        if match_data:
            participant_info_list = extract_match_info(match_data, match2_id)
            all_participant_info.extend(participant_info_list)
            x += 1
            print(f"Processed matches: {x}")
            
            if x % 100 == 0:
                print("Sleeping for 100 seconds to avoid rate limit...")
                time.sleep(100)

print("Data collection complete")

# プレイヤーデータフレーム
df_main_participants = pd.DataFrame(all_participant_info)

# 結果の表示
print(df_main_participants.head())

Processed matches: 1
Processed matches: 2
Processed matches: 3
Processed matches: 4
Processed matches: 5
Processed matches: 6
Processed matches: 7
Processed matches: 8
Processed matches: 9
Processed matches: 10
Processed matches: 11
Processed matches: 12
Processed matches: 13
Processed matches: 14
Processed matches: 15
Processed matches: 16
Processed matches: 17
Processed matches: 18
Processed matches: 19
Processed matches: 20
Processed matches: 21
Processed matches: 22
Processed matches: 23
Processed matches: 24
Processed matches: 25
Processed matches: 26
Processed matches: 27
Processed matches: 28
Processed matches: 29
Processed matches: 30
Processed matches: 31
Processed matches: 32
Processed matches: 33
Processed matches: 34
Processed matches: 35
Processed matches: 36
Processed matches: 37
Processed matches: 38
Processed matches: 39
Processed matches: 40
Processed matches: 41
Processed matches: 42
Processed matches: 43
Processed matches: 44
Processed matches: 45
Processed matches: 

In [516]:
df_main_participants

match_id  game_duration  champion_id  kills  deaths  assists  \
0       KR_7115283387           1554          104      0       6        0   
1       KR_7115283387           1554           63      7       8       11   
2       KR_7115283387           1554          110     10       8        4   
3       KR_7115283387           1554          555     11      10        7   
4       KR_7115283387           1554           14      9       6       12   
...               ...            ...          ...    ...     ...      ...   
287627  KR_7100065963           1955          516      3       8        8   
287628  KR_7100065963           1955          121      5       5        7   
287629  KR_7100065963           1955          134      6      11        6   
287630  KR_7100065963           1955          221     10      10       12   
287631  KR_7100065963           1955          117      3      10       22   

        total_damage_dealt  gold_earned  vision_score  win  team_id  
0                    50665         5760             0    0      200  
1                    94686        13508             0    1      100  
2                   117277        13004             0    1      100  
3                   117207        16060             0    1      100  
4                   134661        17752             0    1      100  
...                    ...          ...           ...  ...      ...  
287627              100385         9984            14    0      200  
287628              213659        11981            21    0      200  
287629              226351        12678            18    0      200  
287630              280355        17112            25    0      200  
287631               30577         9128           100    0      200  

[287632 rows x 11 columns]

In [511]:
x

420

In [454]:
df_participants.to_csv('data.csv', index=False)

In [455]:
test_matchlist

['KR_7107364029',
 'KR_7107302105',
 'KR_7107262350',
 'KR_7107234039',
 'KR_7106549720',
 'KR_7106476804',
 'KR_7106450061',
 'KR_7106405274',
 'KR_7106367267',
 'KR_7106321156',
 'KR_7106296028',
 'KR_7106264680',
 'KR_7106219943',
 'KR_7106200340',
 'KR_7105262687',
 'KR_7105228468',
 'KR_7105208062',
 'KR_7104603785',
 'KR_7104550452',
 'KR_7104519140',
 'KR_7104455030',
 'KR_7104368461',
 'KR_7104318051',
 'KR_7104248909',
 'KR_7104213802',
 'KR_7104153767',
 'KR_7104092460',
 'KR_7104054819',
 'KR_7104014193',
 'KR_7103480767',
 'KR_7103486022',
 'KR_7103472471',
 'KR_7103464600',
 'KR_7103453917',
 'KR_7103452361',
 'KR_7103446210',
 'KR_7103440080',
 'KR_7103281353',
 'KR_7103231135',
 'KR_7103111716',
 'KR_7103052271',
 'KR_7102964765',
 'KR_7102911203',
 'KR_7102825103',
 'KR_7102774110',
 'KR_7102313802',
 'KR_7102254856',
 'KR_7102213539',
 'KR_7102184567',
 'KR_7101863165',
 'KR_7101853405',
 'KR_7101835842',
 'KR_7101823914',
 'KR_7101807929',
 'KR_7101798114',
 'KR_71017

In [470]:
df_grouped = df_participants.groupby(['match_id', 'team_id']).agg({
    'champion_id': list,  # チャンピオンIDをリスト形式でまとめる
    'gold_earned': 'sum',  # 合計ゴールド
    'total_damage_dealt': 'sum',  # 合計ダメージ
    'vision_score': 'sum',  # 合計ヴィジョンスコア
    'kills': 'sum',  # 合計キル
    'deaths': 'sum',  # 合計デス
    'assists': 'sum'  # 合計アシスト
}).reset_index()

# カラム名の調整
df_grouped.columns = ['match_id', 'team_id', 'champion_ids', 'team_gold', 'team_damage', 'team_vision', 'team_kills', 'team_deaths', 'team_assists']

# チーム1とチーム2の統計情報を同じ行にまとめる
df_wide = df_grouped.pivot(index='match_id', columns='team_id', values=['champion_ids', 'team_gold', 'team_damage', 'team_vision', 'team_kills', 'team_deaths', 'team_assists'])

# カラム名のフラット化
df_wide.columns = [f'{stat}_{team}' for stat, team in df_wide.columns]
df_wide.reset_index(inplace=True)

print("\nProcessed DataFrame:")
print(df_wide.head())


Processed DataFrame:
        match_id          champion_ids_100         champion_ids_200  \
0  KR_7098152566   [24, 76, 166, 145, 111]    [23, 876, 18, 22, 16]   
1  KR_7098192332  [80, 104, 142, 429, 412]  [897, 76, 136, 22, 111]   
2  KR_7098229887    [72, 9, 126, 145, 518]   [54, 163, 18, 429, 60]   
3  KR_7098330694    [2, 203, 163, 523, 53]   [85, 104, 22, 18, 555]   
4  KR_7098380149   [75, 254, 84, 222, 117]   [85, 121, 23, 221, 99]   

  team_gold_100 team_gold_200 team_damage_100 team_damage_200 team_vision_100  \
0         36013         25688          347755          279060              76   
1         27406         34550          226298          310234              65   
2         41208         52555          438362          573835             139   
3         25719         37171          234452          314165              62   
4         60125         53107          830908          786090             195   

  team_vision_200 team_kills_100 team_kills_200 team_deaths_100 

In [474]:

# マッチIDごとにグループ化して処理
df_grouped2 = df_participants.groupby(['match_id', 'team_id']).agg({
    'champion_id': list,  # チャンピオンIDをリスト形式でまとめる
    'gold_earned': 'sum',  # 合計ゴールド
    'total_damage_dealt': 'sum',  # 合計ダメージ
    'vision_score': 'sum',  # 合計ヴィジョンスコア
    'kills': 'sum',  # 合計キル
    'deaths': 'sum',  # 合計デス
    'assists': 'sum'  # 合計アシスト
}).reset_index()

# カラム名の調整
df_grouped2.columns = ['match_id', 'team_id', 'champion_ids', 'team_gold', 'team_damage', 'team_vision', 'team_kills', 'team_deaths', 'team_assists']

# チーム1とチーム2の統計情報を同じ行にまとめる
df_wide2 = df_grouped2.pivot(index='match_id', columns='team_id', values=['champion_ids', 'team_gold', 'team_damage', 'team_vision', 'team_kills', 'team_deaths', 'team_assists'])

# カラム名のフラット化
df_wide2.columns = [f'{stat}_{team}' for stat, team in df_wide2.columns]
df_wide2.reset_index(inplace=True)

print("\nProcessed DataFrame with Lists:")
print(df_wide2.head())

# チャンピオンIDのリストを個別のカラムに展開
max_champions = 5  # 1チームあたりの最大チャンピオン数（ここでは10と仮定）

for team in [100, 200]:
    for i in range(max_champions):
        df_wide2[f'champion_{team}_{i+1}'] = df_wide2[f'champion_ids_{team}'].apply(lambda x: x[i] if i < len(x) else np.nan)

# 不要なカラムの削除
df_wide2.drop(columns=[f'champion_ids_{team}' for team in [100, 200]], inplace=True)

print("\nProcessed DataFrame without Lists:")
print(df_wide2.head())


Processed DataFrame with Lists:
        match_id          champion_ids_100         champion_ids_200  \
0  KR_7098152566   [24, 76, 166, 145, 111]    [23, 876, 18, 22, 16]   
1  KR_7098192332  [80, 104, 142, 429, 412]  [897, 76, 136, 22, 111]   
2  KR_7098229887    [72, 9, 126, 145, 518]   [54, 163, 18, 429, 60]   
3  KR_7098330694    [2, 203, 163, 523, 53]   [85, 104, 22, 18, 555]   
4  KR_7098380149   [75, 254, 84, 222, 117]   [85, 121, 23, 221, 99]   

  team_gold_100 team_gold_200 team_damage_100 team_damage_200 team_vision_100  \
0         36013         25688          347755          279060              76   
1         27406         34550          226298          310234              65   
2         41208         52555          438362          573835             139   
3         25719         37171          234452          314165              62   
4         60125         53107          830908          786090             195   

  team_vision_200 team_kills_100 team_kills_200 team_

In [490]:
df_wide2.to_csv('test.csv', index=False)

In [519]:

# マッチIDごとにグループ化して処理
df_main_grouped = df_main_participants.groupby(['match_id', 'team_id']).agg({
    'champion_id': list,  # チャンピオンIDをリスト形式でまとめる
    'gold_earned': 'sum',  # 合計ゴールド
    'total_damage_dealt': 'sum',  # 合計ダメージ
    'vision_score': 'sum',  # 合計ヴィジョンスコア
    'kills': 'sum',  # 合計キル
    'deaths': 'sum',  # 合計デス
    'assists': 'sum',  # 合計アシスト
    'win': 'max'  # 勝利情報を保持
}).reset_index()

# カラム名の調整
df_main_grouped.columns = ['match_id', 'team_id', 'champion_ids', 'team_gold', 'team_damage', 'team_vision', 'team_kills', 'team_deaths', 'team_assists', 'win']

# チーム1とチーム2の統計情報を同じ行にまとめる
df_wide = df_main_grouped.pivot(index='match_id', columns='team_id', values=['champion_ids', 'team_gold', 'team_damage', 'team_vision', 'team_kills', 'team_deaths', 'team_assists'])

# カラム名のフラット化
df_wide.columns = [f'{stat}_{team}' for stat, team in df_wide.columns]
df_wide.reset_index(inplace=True)

# 勝利情報を保持（チーム100の勝利情報を基にする）
df_wide['win'] = df_main_grouped[df_main_grouped['team_id'] == 100].set_index('match_id')['win'].reindex(df_wide['match_id']).values

# チャンピオンIDのリストを個別のカラムに展開
max_champions = 5  # 1チームあたりの最大チャンピオン数

for team in [100, 200]:
    for i in range(max_champions):
        df_wide[f'champion_{team}_{i+1}'] = df_wide[f'champion_ids_{team}'].apply(lambda x: x[i] if i < len(x) else np.nan)

# 不要なカラムの削除
df_wide.drop(columns=[f'champion_ids_{team}' for team in [100, 200]], inplace=True)

print("\nProcessed DataFrame without Lists:")
print(df_wide.head())



Processed DataFrame without Lists:
        match_id team_gold_100 team_gold_200 team_damage_100 team_damage_200  \
0  KR_7073378667         32884         25236          324871          266104   
1  KR_7073468096         45131         56803          641412          687396   
2  KR_7073500163         87495         84225         1350107         1329850   
3  KR_7076789963         54192         38831          634855          425239   
4  KR_7076901467         73244         75942          906951          985184   

  team_vision_100 team_vision_200 team_kills_100 team_kills_200  \
0              70              81             16              8   
1             111             151             14             31   
2             224             293             41             44   
3             164             150             32             11   
4             265             242             42             34   

  team_deaths_100  ... champion_100_1 champion_100_2 champion_100_3  \
0        

In [520]:
df_wide.to_csv('main.csv', index=False)

In [530]:
# 全ての特徴量を使って学習データを準備
X = df_wide.drop(columns=['match_id', 'win'])
y = df_wide['win']

# 訓練データとテストデータの分割
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [14]:
# モデルの学習
clf = RandomForestClassifier(n_estimators=100, random_state=42)
clf.fit(X_train, y_train)

# テストデータでの予測と精度の計算
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f'Accuracy: {accuracy:.4f}')

NameError: name 'X_train' is not defined

In [534]:
model_filename = 'lolperfect_AI.pkl'
joblib.dump(clf, model_filename)

['lolperfect_AI.pkl']

In [5]:
# 精度テスト
file_path = 'main.csv'
df = pd.read_csv(file_path)

# 保持するカラム
columns_to_keep = ['win', 'champion_100_1', 'champion_100_2', 'champion_100_3', 'champion_100_4', 'champion_100_5',
                   'champion_200_1', 'champion_200_2', 'champion_200_3', 'champion_200_4', 'champion_200_5']

# すべてのカラムを取得
all_columns = df.columns

# 保持するカラム以外のカラムをゼロに設定
for col in all_columns:
    if col not in columns_to_keep:
        df[col] = 0

# 結果のデータフレームを表示
print(df)

# 必要に応じて結果を新しいCSVファイルに保存
df.to_csv('output_file.csv', index=False)

       match_id  team_gold_100  team_gold_200  team_damage_100  \
0             0              0              0                0   
1             0              0              0                0   
2             0              0              0                0   
3             0              0              0                0   
4             0              0              0                0   
...         ...            ...            ...              ...   
13957         0              0              0                0   
13958         0              0              0                0   
13959         0              0              0                0   
13960         0              0              0                0   
13961         0              0              0                0   

       team_damage_200  team_vision_100  team_vision_200  team_kills_100  \
0                    0                0                0               0   
1                    0                0                

In [6]:
test_X = df.drop(columns=['match_id', 'win'])
test_y = df['win']

In [15]:
# テストデータでの予測と精度の計算
with open('lolperfect_AI.pkl', 'rb') as file:
    clf = pickle.load(file)

y_pred = clf.predict(test_X)
accuracy = accuracy_score(test_y, y_pred)
print(f'Accuracy: {accuracy:.4f}')

UnicodeDecodeError: 'utf-8' codec can't decode byte 0x80 in position 0: invalid start byte